In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
import jax
import pickle
from atari import AtariEnv
from networks import AtariiDQN, AtariiIQN
from networks import AtariiIQN

# ------- START TO MODIFY ------- #
IDQN_ALGO = True # if False then i-IQN is evaluated
GAME = "Alien"
NETWORK_SEED = 1 # seed in [1, 2, 3, 4, 5]
EVALUATION_SEED = 0
HORIZON = 27000
ENDING_EPS = 0.01
RECORD_VIDEO = False

### 56 games are available for i-DQN with 5 seeds each:
# Alien, Amidar, Assault, Asterix, Asteroids, Atlantis, 
# BankHeist, BattleZone, BeamRider, Berzerk, Bowling, Boxing, Breakout, Centipede, 
# ChopperCommand, CrazyClimber, DemonAttack, DoubleDunk, Enduro, FishingDerby, 
# Freeway, Frostbite, Gopher, Gravitar, Hero, IceHockey, Jamesbond, Kangaroo, 
# Krull, KungFuMaster, MontezumaRevenge, MsPacman, NameThisGame, Phoenix, Pitfall, 
# Pong, Pooyan, PrivateEye, Qbert, Riverraid, RoadRunner, Robotank, Seaquest, Skiing, 
# Solaris, SpaceInvaders, StarGunner, Tennis, TimePilot, Tutankham, UpNDown, Venture, 
# VideoPinball, WizardOfWor, YarsRevenge, Zaxxon

## 20 games are available for i-IQN with 5 seeds each:
# Alien, Assault, BankHeist, Berzerk, Breakout, Centipede, 
# ChopperCommand, DemonAttack, Enduro, Frostbite, Gopher, 
# Gravitar, IceHockey, Jamesbond, Krull, KungFuMaster, 
# Riverraid, Seaquest, Skiing, StarGunner
# ------- END TO MODIFY ------- #


params_path = f"parameters/{GAME}/{'iDQN' if IDQN_ALGO else 'iIQN'}/{5 if IDQN_ALGO else 3}_Q_{NETWORK_SEED}_best_online_params"

env = AtariEnv(GAME)

if IDQN_ALGO:
    q = AtariiDQN(env.n_actions, idx_head=0) # idx_head in [0, 1, 2, 3, 4, 5]
else:
    q = AtariiIQN(env.n_actions, idx_head=0) # idx_head in [0, 1, 2, 3]

with open(params_path, "rb") as handle:
    q_params = pickle.load(handle)

reward, absorbing = env.evaluate_one_simulation(
    q, q_params, HORIZON, ENDING_EPS, jax.random.PRNGKey(EVALUATION_SEED), params_path if RECORD_VIDEO else None
)
print("Undiscounted reward:", reward)
print("N steps", env.n_steps, "; Horizon", HORIZON, "; Absorbing", absorbing)